## Statistical Learning Theory Lab: Recommender System

René Gesele 
168039
rene.gesele@uni-jena.de
02.08.2019

In [1]:
import numpy as np

# read train set and qualifying set
Xq = np.genfromtxt("data/data_qualifying_blanc.csv", delimiter=",", dtype=np.int)
Xt = np.genfromtxt("data/data_train.csv", delimiter=",", dtype=np.int)
print(Xq)

# predict ratings
mean = np.mean(Xt[:, 2])
Xq_mean = np.append(Xq, np.full((Xq.shape[0], 1), mean), axis=1)

# save in right format
np.savetxt("qualifying_mean.csv", Xq_mean,
           delimiter=",", newline="\n", encoding="utf-8")

[[3728  815]
 [1714  398]
 [1781  757]
 ...
 [  13 1188]
 [1899  432]
 [ 314  847]]


In [2]:
sparsematrix = np.zeros((max(Xt[:, 0]+1), max(Xt[:, 1])+1))
spcol = len(sparsematrix[0,:])
sprow = len(sparsematrix[:, 0])
print(spcol)
print(sprow)

2080
5499


In [3]:
for i in range(len(Xt[:, ])):
    user = Xt[i, 0]
    item = Xt[i, 1]
    rating = Xt[i, 2]
    sparsematrix[user, item] = rating+1

In [4]:
# euclidic norm of a vector
def euklidnorm(vec):
    tmp = 0
    for i in vec:
        tmp+=i**2
    return np.sqrt(tmp)

# Cosine-similarity
def cosim(user1, user2):
    return np.dot(user1, user2)/(euklidnorm(user1)*euklidnorm(user2))

# returns mean of given raitings by a user
def mean_of_given_ratings(user):
    sum_of_none_zero = 0
    count = 0
    for i in user:
        if i != 0:
            count+=1
            sum_of_none_zero += i
    return sum_of_none_zero/count
            
            
            
# Pearson-similarity
def pearson(user1, user2):
    user1_mean = mean_of_given_ratings(user1)
    user2_mean = mean_of_given_ratings(user2)
    for i in range(len(user1)):
        user1[i] = user1[i] - user1_mean
        user2[i] = user2[i] - user2_mean
    cosim(user1,user2)
    return cosim(user1,user2)

# deletes rows and columns that are 0 only
# returns three matrices, one desparsed matrix and two matrices that safe indices of kept entries
def desparse(user_item_matrix):
    copy = user_item_matrix
    
    row_index = np.zeros((user_item_matrix.shape[0], user_item_matrix.shape[1]))
    column_index = row_index
    for i in range(row_index.shape[0]):
        row_index[i,:] = i
    for i in range(column_index.shape[1]):
        column_index[:,i] = i
    
    i = 0 
    j = 0
    br0 = copy.shape[0]
    br1 = copy.shape[1]
    
    while i < br0 : 
        if all(copy[i]==0):
            copy = np.delete(copy, i, 0)
            row_index = np.delete(row_index, i, 0)
            column_index = np.delete(column_index, i, 0)
            br0-=1
        else:
            
            i+=1
    print("halftime")
    while j < br1 :
        if all(copy[:,j]==0):
            copy = np.delete(copy, j, 1)
            row_index = np.delete(row_index, j, 1)
            column_index = np.delete(column_index, j, 1)
            br1-=1
            
        else:
            
            j+=1
    return copy, row_index, column_index


def user_distance_matrix(user_item_matrix, sim):
    user_dist = np.zeros((user_item_matrix.shape[0], user_item_matrix.shape[0]))
    for i in range(len(user_item_matrix)):
        for j in range(i, len(user_item_matrix)):
            
            if i == j:
                user_dist[i][j] = 0
            else:
                user_dist[i][j] = sim(user_item_matrix[i], user_item_matrix[j])
    return user_dist



def fill_zeros_with_mean(user_item_matrix):
    copy = user_item_matrix
    for i in range(copy.shape[0]):
        for j in range(copy.shape[1]):
            if copy[i,j] == 0:
                copy[i,j] = mean
            
    return copy

#macht aus der halben user_distance_matrix eine symmetrische um zeilenweise die Distanzen von usern extrahieren zu können
def make_symmetric_matrix(half_matrix):
    matrix = np.transpose(half_matrix)
    for i in range(matrix.shape[0]):
        for j in range(i, matrix.shape[0]):
            matrix[i][j] = matrix[j][i]
    return matrix;
                
#knn returns list of indices of the user_item_matrix
def knn(user_index,  user_distance_matrix, k):
    nn = []
    for i in range(user_distance_matrix.shape[0]):
        if user_index != i:
            tmp = user_distance_matrix[user_index][i]
            
            if len(nn)<k:
                nn.append((i, tmp))
                
            else:
                if tmp > nn[-1][1]:
                    nn[-1] = (i, tmp)
            nn = sorted(nn, reverse = True,  key = lambda el: el[1])
    return [x[0] for x in nn]



#returns indices of knn 
def matrix_of_knn(user_distance_matrix):
    matrix = []
    for i in range(user_distance_matrix.shape[0]):
        tmp = knn(i, user_distance_matrix, user_distance_matrix.shape[0])
        matrix.append(tmp)
    return matrix

#returns a user to each indices in list_of_indices 
def index_to_user(list_of_indices, user_item_matrix):
    copy = []
    for i in range(len(list_of_indices)):
        copy.append(user_item_matrix[i])
    return copy

#calculate expected ratings for one user 

def predict_rating(user_index, list_of_indices, distance_matrix, user_item_matrix, k):
    copy = user_item_matrix
    user = user_item_matrix[user_index]
    print("test")
    r_hat = mean_of_given_ratings(user)
    for i in range(len(user)):
        print("test2")
        if user_item_matrix[user_index][i]==0:
            print("test3")
            sum_of_rating = 0
            sum_of_sim = 0
            tlist = []
            for j in range(len(list_of_indices)):
                if (user_item_matrix[int(list_of_indices[j])][i]>0) & (len(tlist)<=k):
                    tlist.append(list_of_indices[j])
    
            for j in range(len(tlist)):
                simuv = distance_matrix[user_index][j]
                sum_of_rating += simuv*(user_item_matrix[int(tlist[j])][i] - mean_of_given_ratings(user_item_matrix[int(tlist[j])]))
                sum_of_sim += np.abs(simuv)
            
           
            copy[user_index][i] = r_hat + sum_of_rating/sum_of_sim
            print(copy[user_index][i])
    return copy



#calculates all rating for each user and item combination that is not given
def prediction_matrix(user_item_matrix, distance_matrix, matrix_of_knn_indices, k):
    copy = user_item_matrix
    for i in range(user_item_matrix.shape[0]):
        copy = predict_rating(i, matrix_of_knn_indices[i], distance_matrix, user_item_matrix, k)
    return copy


        
# inputs 0-rows and columns to get original shape      
def rebuild_user_item_matrix(user_item_matrix, sparsematrix, row_index, column_index):
    copy = sparsematrix
    for i in range(user_item_matrix.shape[0]):
        for j in range(user_item_matrix.shape[1]):
            copy[row_index[i][j]][column_index[i][j]] = user_item_matrix[i][j]
    return copy

# gets the prediction values for all user item combinations in test_data 
def get_predictions_for_test_data(user_item_matrix, test_data):
    tmp = []
    for i in range(len(test_data)):
        tmp.append(user_item_matrix[test_data[i][0]-1][test_data[i][1]-1])
           
    tmp = np.asarray(tmp)
    print(tmp.shape)
    
    test_data = np.append(test_data, np.reshape(tmp, (test_data.shape[0], 1)), axis = 1)
    for i in range(len(test_data)):
        if test_data[i][2]>= 0:
            test_data[i][2] = test_data[i][2]-1
        else: 
            test_data[i][2] = 0
    print(test_data.shape)
    return(test_data)


In [6]:
# create debug_data
def create_dummy(length, width):        
    debug = np.zeros((length, width))
    for i in range(debug.shape[0]):
        for j in range(debug.shape[1]):
            if (i==0) and (j==0):
                debug[i][j]=0
            elif(i==0) and (j!=0):
                debug[i][j]=i+j
            else:
                debug[i][j]=i+j
    return debug

#debug2 = user_item_matrix    

In [7]:
debug = create_dummy(4,2)
debug_dist = user_distance_matrix(debug,cosim)
print(debug_dist)
debug_dist = make_symmetric_matrix(debug_dist)
print(debug_dist)
debug_mknn = matrix_of_knn(debug_dist) 
print(debug_mknn)
debug_pred = prediction_matrix(debug, debug_dist, debug_mknn, 3)
print(debug_pred)

[[0.         0.89442719 0.83205029 0.8       ]
 [0.         0.         0.99227788 0.98386991]
 [0.         0.         0.         0.99846035]
 [0.         0.         0.         0.        ]]
[[0.         0.89442719 0.83205029 0.8       ]
 [0.89442719 0.         0.99227788 0.98386991]
 [0.83205029 0.99227788 0.         0.99846035]
 [0.8        0.98386991 0.99846035 0.        ]]
[[1, 2, 3], [2, 3, 0], [3, 1, 0], [2, 1, 0]]
test
test2
test3
0.5
test2
test
test2
test2
test
test2
test2
test
test2
test2
[[0.5 1. ]
 [1.  2. ]
 [2.  3. ]
 [3.  4. ]]


In [8]:
user_item_matrix, deleted_rows, deleted_columns = desparse(sparsematrix)


halftime


In [8]:
#user_distances = user_distance_matrix(user_item_matrix, cosim)

In [ ]:
#user_mknn = matrix_of_knn(user_distances)
#np.savetxt("matrix_of_knn.csv", user_mknn, delimiter=",")

In [ ]:
#user_distances = make_symmetric_matrix(user_distances)
#np.savetxt("user_item_distance.csv", user_distances, delimiter=",")

In [9]:
user_mknn =np.genfromtxt("matrix_of_knn.csv", delimiter=",", dtype=np.float)
#print(user_distances)

In [10]:
user_distances = np.genfromtxt("user_item_distance.csv", delimiter=",", dtype=np.float)

In [ ]:
Xq = np.genfromtxt("data/data_qualifying_blanc.csv", delimiter=",", dtype=np.int)
user_based = prediction_matrix(user_item_matrix, user_distances, user_mknn, 1)
rebuild_uim = rebuild_user_item_matrix(user_based, sparsematrix, deleted_rows.astype(int), deleted_columns.astype(int))
filled_rebuild = fill_zeros_with_mean(rebuild_uim)
Xq = get_predictions_for_test_data(filled_rebuild, Xq)
np.savetxt("qualifying_mean.csv", Xq, delimiter=",", newline="\n", encoding="utf-8")

test
test2
test3
2.9
test2
test3
3.1142857142857143
test2
test3
1.9
test2
test3
1.9666666666666668
test2
test3
2.9555555555555553
test2
test3
2.597286012526096
test2
test3
2.1735849056603773
test2
test3
-0.3168894289185906
test2
test3
0.6831105710814094
test2
test3
1.597286012526096
test2
test3
2.943795620437956
test2
test3
0.6831105710814094
test2
test3
2.597286012526096
test2
test3
0.6831105710814094
test2
test3
2.6831105710814094
test2
test3
2.597286012526096
test2
test3
2.6831105710814094
test2
test3
0.6307692307692307
test2
test3
2.6831105710814094
test2
test3
1.6307692307692307
test2
test3
0.9437956204379558
test2
test3
2.6941176470588233
test2
test3
1.943795620437956
test2
test3
2.597286012526096
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
1.6831105710814094
test2
test3
2.6831105710814094
test2
test3
2.943795620437956
test2
test3
2.943795620437956
test2
test3
2.597286012526096
test2
test3
2.943795620437956
test2
test3


3.353488372093023
test2
test3
2.6831105710814094
test2
test3
2.597286012526096
test2
test3
1.597286012526096
test2
test3
2.597286012526096
test2
test3
2.597286012526096
test2
test3
3.2378378378378376
test2
test3
2.911627906976744
test2
test3
2.6831105710814094
test2
test3
2.4834248079034027
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
2.597286012526096
test2
test3
2.3375
test2
test3
2.597286012526096
test2
test3
2.597286012526096
test2
test3
2.6941176470588233
test2
test3
3.1142857142857143
test2
test3
2.597286012526096
test2
test3
2.597286012526096
test2
test3
1.597286012526096
test2
test3
2.597286012526096
test2
test3
1.5052631578947366
test2
test3
2.986932447397564
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
3.0666666666666664
test2
test3
2.6831105710814094
test2
test3
1.597286012526096
test2
test3
3.3577464788732394
test2
test3
2.986932447397564
test2
test3
2.0065573770491802
test2
test3
2.597286012526096
test2
test3
2.5972

2.597286012526096
test2
test3
1.9555555555555553
test2
test3
2.597286012526096
test2
test3
2.3591836734693876
test2
test3
2.3591836734693876
test2
test3
2.597286012526096
test2
test3
2.986932447397564
test2
test3
2.597286012526096
test2
test3
2.597286012526096
test2
test3
2.597286012526096
test2
test3
2.597286012526096
test2
test3
3.8754098360655735
test2
test3
2.493333333333333
test2
test3
2.597286012526096
test2
test3
3.0727272727272728
test2
test3
1.0065573770491802
test2
test3
3.537254901960784
test2
test3
1.8754098360655735
test2
test3
2.597286012526096
test2
test3
2.986932447397564
test2
test3
2.597286012526096
test2
test3
2.597286012526096
test2
test3
2.597286012526096
test2
test3
2.9
test2
test3
2.966666666666667
test2
test3
2.597286012526096
test2
test3
1.5372549019607842
test2
test3
2.597286012526096
test2
test3
1.9
test2
test3
3.2378378378378376
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
2.597286012526096
test2
test3
1.9869324473975636
test2
te

2.597286012526096
test2
test3
2.6831105710814094
test2
test3
2.342857142857143
test2
test3
2.342857142857143
test2
test3
3.036363636363636
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
2.6831105710814094
test2
test3
3.0727272727272728
test2
test3
3.342857142857143
test2
test3
2.0129032258064514
test2
test3
2.507142857142857
test2
test3
3.0065573770491802
test2
test3
2.275
test2
test3
0.522743682310469
test2
test3
3.275
test2
test3
2.597286012526096
test2
test3
2.911627906976744
test2
test3
2.957142857142857
test2
test3
3.0065573770491802
test2
test3
2.65
test2
test3
2.65
test2
test3
0.522743682310469
test2
test3
2.957142857142857
test2
test3
3.036363636363636
test2
test3
2.1999999999999997
test2
test2
test2
test3
2.0666666666666664
test2
test3
3.0666666666666664
test2
test3
2.4
test2
test3
2.0727272727272728
test2
test3
2.88
test2
test3
2.6831105710814094
test2
test3

2.597286012526096
test2
test3
2.597286012526096
test2
test3
2.749322210636079
test2
test3
2.597286012526096
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
1.6831105710814094
test2
test3
0.9869324473975636
test2
test3
0.9869324473975636
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
1.9869324473975636
test2
test3
1.9869324473975636
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
3.157837837837838
test2
test3
2.986932447397564
test2
test3
2.945766590389016
test2
test3
2.749322210636079
test2
test3
2.986932447397564
test2
test3
2.749322210636079
test2
test3
2.986932447397564
test2
test3
2.986932447397564
test2
test3
2.749322210636079
test2
test3
2.986932447397564
test2
test3
2.749322210636079
test2
test3
1.986

...

nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test

nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test

nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test2
test3
nan
test

3.404412518755923
test2
test3
3.2934495225411995
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.2191573042713135
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.431304143164918
test2
test3
3.404412518755923
test2
test3
3.3916348485516292
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.431304143164918
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.3301203004860365
test2
test3
3.3916348485516292
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.3916348485516292
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.4397623212437876
test2
test3
3.431304143164918
test2
test3
2.515375514970646
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.431304143164918
test2
test3
3.4

3.431304143164918
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.431304143164918
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.653324441314126
test2
test3
3.404412518755923
test2
test3
3.3916348485516292
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.431304143164918
test2
test3
3.3916348485516292
test2
test3
3.3595176799369755
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.3916348485516292
test2
test3
3.404412518755923
test2
test3
3.431304143164918
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.3916348485516292
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.4410832967007594
test2
test3
3.431304143164918
test2
test3
3.404412518755923
test2
test3
3.404412518755923
test2
test3
3.4410832967007594
test2
test3
3.404412518755923
test2
test3
3.3

In [ ]:
#Xq2 = np.genfromtxt("data/data_qualifying_blanc.csv", delimiter=",", dtype=np.int)
#user_based_prediction = prediction_matrix_zero(user_item_matrix, user_distances,5)
#rebuild_next_level = rebuild_user_item_matrix(user_based_prediction, sparsematrix, deleted_rows.astype(int), deleted_columns.astype(int))
#filled_rebuild2 = fill_zeros_with_mean(rebuild_next_level)
#Xq2 = get_predictions_for_test_data(filled_rebuild2, Xq2)
#np.savetxt("qualifying_mean_2.csv", Xq2, delimiter=",", newline="\n", encoding="utf-8")


In [ ]:
#for i in range(len(Xq)):
#    print(Xq[i][2])

for i in range(len(Xq)):
    if (Xq[i][2] == 5.0):
        print("5.0: ", i)
    if (Xq[i][2] == None):
        print("nan: ", i )

In [ ]:
np.savetxt("qualifying_mean.csv", Xq, delimiter=",", newline="\n", encoding="utf-8")

In [12]:
print(np.mean(Xq[:,2]))

-0.4020680162760743


In [15]:
count_minus = 0
count_plus = 0
for i in range(len(Xq[:,2])):
    if Xq[i][2]<0:
        count_minus+=1
    else:
        count_plus +=1
print(count_minus)
print(count_plus)

86732
21928


Die Methoden hier drüber hatten zunächst nicht nach den k nächsten Nachbar mit eingetragenem Rating gesucht, sonder immer die gleich top-k verwendet. 
Hier drunter ist der notdürftige versuch das zu fixen. (Rechenzeit geht durch die Decke)

In [ ]:
# calculate knn under the condition that for an item the rating of the neighbours is not zero
def knn_none_zero(user_index,  user_distance_matrix, k, user_item_matrix, item):
    nn = []
    for i in range(user_distance_matrix.shape[0]):
        if (user_index != i) & (user_item_matrix[user_index][item]!=0):
            tmp = user_distance_matrix[user_index][i]
            
            if len(nn)<k:
                nn.append((i, tmp))
                
            else:
                if tmp > nn[-1][1]:
                    nn[-1] = (i, tmp)
            nn = sorted(nn, reverse = True,  key = lambda el: el[1])
    return [x[0] for x in nn]

#calculate an expected rating for one user with the condition that each neighbour rated the item
def predict_rating_zero(user_index, distance_matrix, user_item_matrix, k):
    copy = user_item_matrix
    user = user_item_matrix[user_index]
    r_hat = np.mean(user)
    for i in range(len(user)):
        list_of_users = index_to_user(knn_none_zero(user_index, distance_matrix, k,user_item_matrix, i), user_item_matrix)
        if user_item_matrix[user_index][i]==0:
            sum_of_rating = 0
            sum_of_sim = 0
            for j in range(len(list_of_users)):
                simuv = distance_matrix[user_index][j]
                
                sum_of_rating += simuv*(list_of_users[j][i] - np.mean(list_of_users[j]))
                sum_of_sim += np.abs(simuv)
            user[i] = r_hat + sum_of_rating/sum_of_sim
    return copy

# has the condition that neighbours rated the item
def prediction_matrix_zero(user_item_matrix, distance_matrix, k):
    copy = user_item_matrix
    for i in range(user_item_matrix.shape[0]):
        copy = predict_rating_zero(i, distance_matrix, user_item_matrix, k)
    return copy